In [1]:
from google import genai
from google.genai import types
from datetime import datetime
from pydantic import BaseModel
import os

class JobSuggestion(BaseModel):
    company_name: str
    company_description: str
    job_title: str
    application_text: str

# Load CV from file
with open("cv_sebastian_egli.txt", "r", encoding="utf-8") as f:
    cv = f.read()

# Load already suggested companies from file (to avoid duplicates)
with open("already_suggested_companies.txt", "r", encoding="utf-8") as f:
    already_suggested_companies = f.read()

# Define boolean for even-numbered days (I want to switch un/solicited every day)
today =   datetime.today()
unsolicited_application = today.day % 2 == 0

if unsolicited_application:
    query = ["""Analysiere meinen Lebenslauf (cv) und die Liste bereits vorgeschlagener Unternehmen (already_suggested_companies). 
Schlage mir genau ein Unternehmen in der Nähe von Marburg vor, das noch nicht in already_suggested_companies enthalten ist 
und für eine Initiativbewerbung besonders gut zu meinem Profil passt. 

Erkläre in maximal 150 Wörtern prägnant, warum dieses Unternehmen eine besonders gute Wahl für mich wäre. 
Formuliere die Antwort als kurze, professionelle Email mit dem Titel: 'Neuer Jobvorschlag'. 
Begründe die Eignung anhand meiner Qualifikationen und Interessen. 
Füge außerdem einen einzelnen Satz hinzu, der direkt in einem Bewerbungsschreiben genutzt werden könnte, 
um die Übereinstimmung zwischen mir und dem Unternehmen hervorzuheben. 

Liefere nur die Email, keine zusätzliche Erklärung.""",already_suggested_companies,cv]
else:
    query = ["""Analysiere meinen Lebenslauf (cv) und die Liste bereits vorgeschlagener Unternehmen (already_suggested_companies). 
Schlage mir genau eine aktuell offene Stellenausschreibung in der Nähe von Marburg vor für ein Unternehmen, das noch nicht in already_suggested_companies enthalten ist 
und die besonders gut zu meinem Profil passt. 

Erkläre in maximal 150 Wörtern prägnant, warum diese Stelle eine besonders gute Wahl für mich wäre. 
Formuliere die Antwort als kurze, professionelle Email mit dem Titel: 'Neuer Jobvorschlag'. 
Begründe die Eignung anhand meiner Qualifikationen und Interessen. 
Füge außerdem einen einzelnen Satz hinzu, der direkt in einem Bewerbungsschreiben genutzt werden könnte, 
um die Übereinstimmung zwischen mir und der ausgeschriebenen Stelle hervorzuheben. 

Liefere nur die Email, keine zusätzliche Erklärung.""",already_suggested_companies,cv]

In [2]:
api_key = os.environ.get("GEMINI_API_KEY")

client = genai.Client(api_key=api_key)

# Step 1: grounded search (necessary for live web search)
resp_grounded = client.models.generate_content(
    model="gemini-2.5-flash",
    contents=query,
    config=types.GenerateContentConfig(
        tools=[types.Tool(google_search=types.GoogleSearch())]
    ),
)

grounded_answer = resp_grounded.text  # freeform answer

In [3]:
# Step 2: convert to JSON
resp_json = client.models.generate_content(
    model="gemini-2.5-flash",
    contents=f"Turn this answer into JSON: {grounded_answer}",
    config=types.GenerateContentConfig(
        response_mime_type="application/json",
        response_schema=JobSuggestion,
    ),
)

In [ ]:
# Append the response to already_suggested_companies.txt
with open("already_suggested_companies.txt", "a", encoding="utf-8") as f:
    f.write("\n" + resp_json.parsed.company_name)

In [5]:
import smtplib
from email.mime.text import MIMEText

gmail_key = os.environ.get("GMAIL_PW")

# Account details
sender = "seb.egli@gmail.com"
recipient = "seb.egli@gmail.com"
password = gmail_key

# Create email
msg = MIMEText(grounded_answer)
msg["From"] = sender
msg["To"] = recipient
msg["Subject"] = "Neuer Jobvorschlag"

# Send email using Gmail's SMTP
with smtplib.SMTP_SSL("smtp.gmail.com", 465) as server:
    server.login(sender, password)
    server.sendmail(sender, recipient, msg.as_string())